In [1]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import pandas as pd 
from pandas_datareader import data
import requests
import re
import urllib
import io
import matplotlib.pyplot as plt
import altair as alt
from vega_datasets import data
alt.data_transformers.disable_max_rows()


DataTransformerRegistry.enable('default')

In [156]:
fdf=pd.DataFrame
#url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR8-'+nodes+'nodes-1writer-1/res_thr'+threads+'.txt'
for cluster in ['GR8','PXC8']:
    for nodes in ['3','5']:
        for threads in ['1','2','4','8','16','64','128','256']:
    #    for threads in ['1']:
            #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-'+nodes+'nodes-1writer-BP25G-1/res_thr'+threads+'.txt'
            url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-'+cluster+'-'+nodes+'nodes-1writer-1/res_thr'+threads+'.txt'
            s=requests.get(url)


            buf=[]
            for line in s.text.splitlines():
                #rint(line)
                if re.match("^[0-9]", line):
                    buf.append(line)

            df = pd.DataFrame([x.split(',') for x in buf])
            df['Nodes'] = nodes
            df['Cluster'] = cluster
            if fdf.empty:
               fdf=df
            else: 
               fdf=fdf.append(df,ignore_index = False)



In [4]:
fdf

0    1        2         3         4         5        6       7  \
0        1    1    49.89   1358.07    615.67    639.62   102.78   44.17   
1        2    1    63.03   1665.82    762.37    777.38   126.06   39.65   
2        3    1    53.00   1756.01    803.00    847.00   106.00   55.82   
3        4    1    67.00   1895.98    867.99    893.99   134.00   33.12   
4        5    1    68.00   1919.99    870.99    912.99   136.00   41.85   
...    ...  ...      ...       ...       ...       ...      ...     ...   
1795  1796  256  3195.99  91039.84  41516.93  43135.93  6386.99  142.39   
1796  1797  256  3197.98  92699.35  42305.70  43993.69  6399.95  116.80   
1797  1798  256  3230.98  91215.42  41598.74  43156.73  6459.96  125.52   
1798  1799  256  3177.94  89545.36  40971.25  42216.22  6357.88  144.97   
1799  1800  256  3230.24  91835.50  41881.20  43494.82  6459.49  116.80   

          8     9 Nodes  
0      1.00  0.00     3  
1      1.00  0.00     3  
2      1.00  0.00     3  
3      0.00  0.00     3  
4      0.00  0.00     3  
...     ...   ...   ...  
1795  15.00  0.00     5  
1796  17.00  0.00     5  
1797  19.00  0.00     5  
1798  18.00  0.00     5  
1799  14.00  0.00     5  

[28800 rows x 11 columns]

In [157]:
fdf.columns =['sec','threads','tps','read','write','other','v1','rt','v3','v4','nodes','cluster']
fdf['tps']=fdf['tps'].astype(float)
fdf['sec']=fdf['sec'].astype(float)
fdf['threads']=fdf['threads'].astype(int)

In [161]:
fdf

sec  threads      tps      read     write     other       v1      rt  \
0        1.0        1    34.92   1107.58    504.90    529.84    72.84   52.89   
1        2.0        1    46.02   1354.66    613.30    649.32    92.04   62.19   
2        3.0        1    44.00   1287.02    580.01    619.01    88.00   56.84   
3        4.0        1    47.00   1373.00    630.00    649.00    94.00   41.10   
4        5.0        1    49.00   1247.00    574.00    575.00    98.00   47.47   
...      ...      ...      ...       ...       ...       ...      ...     ...   
1795  1796.0      256  3195.99  91039.84  41516.93  43135.93  6386.99  142.39   
1796  1797.0      256  3197.98  92699.35  42305.70  43993.69  6399.95  116.80   
1797  1798.0      256  3230.98  91215.42  41598.74  43156.73  6459.96  125.52   
1798  1799.0      256  3177.94  89545.36  40971.25  42216.22  6357.88  144.97   
1799  1800.0      256  3230.24  91835.50  41881.20  43494.82  6459.49  116.80   

         v3    v4 nodes cluster  
0      0.00  0.00     3     GR8  
1      0.00  0.00     3     GR8  
2      0.00  0.00     3     GR8  
3      1.00  0.00     3     GR8  
4      1.00  0.00     3     GR8  
...     ...   ...   ...     ...  
1795  15.00  0.00     5    PXC8  
1796  17.00  0.00     5    PXC8  
1797  19.00  0.00     5    PXC8  
1798  18.00  0.00     5    PXC8  
1799  14.00  0.00     5    PXC8  

[57600 rows x 12 columns]

In [164]:


stripplot =  alt.Chart(fdf.query('nodes == "3" and cluster=="PXC8" and sec>900'), width=100,title='3nodes, threads 1-256').mark_circle(size=8).encode(
    x=alt.X(
        'jitter:Q',
        title=None,
        axis=alt.Axis(values=[0], ticks=True, grid=False, labels=False, title='Threads'),
        scale=alt.Scale(),
    ),
    y=alt.Y('tps:Q',title="Throughput, tps"),
    order='threads:O',
    color=alt.Color('nodes:N', legend=None),
    column=alt.Column(
        'threads:N',
        header=alt.Header(
            labelAngle=0,
            titleOrient='top',
            labelOrient='bottom',
            labelAlign='center',
            labelPadding=10,
        ),
    ),
).transform_calculate(
    # Generate Gaussian jitter with a Box-Muller transform
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).configure_facet(
    spacing=0
).configure_view(
    stroke=None
)

stripplot


alt.Chart(...)

In [167]:
import altair as alt
from vega_datasets import data
alt.data_transformers.disable_max_rows()
from altair.expr import datum

stripplot =  alt.Chart(fdf.query('sec>900 and cluster=="PXC8"'), width=100,title='3 vs 5 nodes, threads 1-256').mark_circle(size=8).encode(
    x=alt.X(
        'jitter:Q',
        title=None,
        axis=alt.Axis(values=[0], ticks=True, grid=False, labels=False),
        scale=alt.Scale(),
    ),
    y=alt.Y('tps:Q', title="Throughput, tps"),
    order='threads:O',
    color='nodes:N',
    facet=alt.Facet('threads:O', columns=5,align="none"),
).transform_calculate(
    # Generate Gaussian jitter with a Box-Muller transform
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).resolve_scale(y='independent').interactive().add_selection(alt.selection_single(empty='all', fields=['nodes']))

#chart = alt.hconcat()
#for threads in ['1','2','4','8','16','64','128','256']:
#    chart |= stripplot.transform_filter(datum.threads == threads)
#chart

stripplot

alt.Chart(...)

In [168]:


alt.Chart(fdf.query('sec>900 and threads=="64" and cluster=="PXC8"'),width=800,title="64 threads").mark_line().encode(
    x='sec',
    y='tps',
    color='nodes',
)



alt.Chart(...)

In [27]:
fdf

sec  threads      tps      read     write     other       v1      rt  \
0        1.0        1    34.92   1107.58    504.90    529.84    72.84   52.89   
1        2.0        1    46.02   1354.66    613.30    649.32    92.04   62.19   
2        3.0        1    44.00   1287.02    580.01    619.01    88.00   56.84   
3        4.0        1    47.00   1373.00    630.00    649.00    94.00   41.10   
4        5.0        1    49.00   1247.00    574.00    575.00    98.00   47.47   
...      ...      ...      ...       ...       ...       ...      ...     ...   
1795  1796.0      256  3195.99  91039.84  41516.93  43135.93  6386.99  142.39   
1796  1797.0      256  3197.98  92699.35  42305.70  43993.69  6399.95  116.80   
1797  1798.0      256  3230.98  91215.42  41598.74  43156.73  6459.96  125.52   
1798  1799.0      256  3177.94  89545.36  40971.25  42216.22  6357.88  144.97   
1799  1800.0      256  3230.24  91835.50  41881.20  43494.82  6459.49  116.80   

         v3    v4 nodes cluster  
0      0.00  0.00     3     GR8  
1      0.00  0.00     3     GR8  
2      0.00  0.00     3     GR8  
3      1.00  0.00     3     GR8  
4      1.00  0.00     3     GR8  
...     ...   ...   ...     ...  
1795  15.00  0.00     5    PXC8  
1796  17.00  0.00     5    PXC8  
1797  19.00  0.00     5    PXC8  
1798  18.00  0.00     5    PXC8  
1799  14.00  0.00     5    PXC8  

[57600 rows x 12 columns]

In [32]:
(fdf.groupby(['cluster','threads','nodes'])['tps']).pct_change().rolling(60).std()*(60**0.5)

0            NaN
1            NaN
2            NaN
3            NaN
4            NaN
          ...   
1795    0.626886
1796    0.625894
1797    0.592038
1798    0.563775
1799    0.563111
Name: tps, Length: 57600, dtype: float64

In [126]:
t1 = fdf.groupby(['cluster','threads','nodes'])['tps']

In [127]:
t1

In [80]:
fdf['pct_groupby'] = fdf.groupby(['cluster','threads','nodes'])['tps'].apply(lambda x: x.pct_change())

In [132]:
import math 
df =  fdf.groupby(['cluster','threads','nodes'])['pct_groupby'].agg(np.std)

In [133]:
df

cluster  threads  nodes
GR8      1        3        0.136352
                  5        6.356265
         2        3        0.144308
                  5        0.375113
         4        3        0.103119
                  5             NaN
         8        3        0.104847
                  5             NaN
         16       3        0.084713
                  5             NaN
         64       3        0.093817
                  5             NaN
         128      3        0.208411
                  5             NaN
         256      3        0.193866
                  5             NaN
PXC8     1        3        0.108422
                  5             NaN
         2        3        0.102637
                  5             NaN
         4        3        0.066300
                  5        0.077449
         8        3        0.065611
                  5        0.076122
         16       3        0.046291
                  5        0.079821
         64       3        0.047387
    

In [145]:
r=fdf.query("cluster=='GR8' and threads==4 and nodes=='5'")['pct_groupby']

In [76]:
fdf

sec  threads      tps      read     write     other       v1      rt  \
0        1.0        1    34.92   1107.58    504.90    529.84    72.84   52.89   
1        2.0        1    46.02   1354.66    613.30    649.32    92.04   62.19   
2        3.0        1    44.00   1287.02    580.01    619.01    88.00   56.84   
3        4.0        1    47.00   1373.00    630.00    649.00    94.00   41.10   
4        5.0        1    49.00   1247.00    574.00    575.00    98.00   47.47   
...      ...      ...      ...       ...       ...       ...      ...     ...   
1795  1796.0      256  3195.99  91039.84  41516.93  43135.93  6386.99  142.39   
1796  1797.0      256  3197.98  92699.35  42305.70  43993.69  6399.95  116.80   
1797  1798.0      256  3230.98  91215.42  41598.74  43156.73  6459.96  125.52   
1798  1799.0      256  3177.94  89545.36  40971.25  42216.22  6357.88  144.97   
1799  1800.0      256  3230.24  91835.50  41881.20  43494.82  6459.49  116.80   

         v3    v4 nodes cluster  shifted  %_groupby  
0      0.00  0.00     3     GR8      NaN        NaN  
1      0.00  0.00     3     GR8    34.92   0.317869  
2      0.00  0.00     3     GR8    46.02  -0.043894  
3      1.00  0.00     3     GR8    44.00   0.068182  
4      1.00  0.00     3     GR8    47.00   0.042553  
...     ...   ...   ...     ...      ...        ...  
1795  15.00  0.00     5    PXC8  3037.08   0.052323  
1796  17.00  0.00     5    PXC8  3195.99   0.000623  
1797  19.00  0.00     5    PXC8  3197.98   0.010319  
1798  18.00  0.00     5    PXC8  3230.98  -0.016416  
1799  14.00  0.00     5    PXC8  3177.94   0.016457  

[57600 rows x 14 columns]

In [30]:
fdf=pd.DataFrame
for nodes in ['3','5']:
#    for threads in ['1','2','4','8','16','64','128','256']:
#    for threads in ['1']:
    #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-'+nodes+'nodes-1writer-BP25G-1/res_thr'+threads+'.txt'
    url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-'+nodes+'nodes-1writer-BP25G-txrate3100-1/res_thr64.txt'
    #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-5nodes-1writer-BP25G-1/res_thr1.txt'
    s=requests.get(url)


    buf=[]
    for line in s.text.splitlines():
        #rint(line)
        if re.match("^[0-9]", line):
            buf.append(line)

    df = pd.DataFrame([x.split(',') for x in buf])
    df['Nodes'] = nodes
    if fdf.empty:
       fdf=df
    else: 
       fdf=fdf.append(df,ignore_index = False)

In [36]:
fdf.columns =['sec','threads','tps','read','write','other','v1','rt','v3','v4','nodes']
fdf['tps']=fdf['tps'].astype(float)
fdf['sec']=fdf['sec'].astype(float)
fdf['rt']=fdf['rt'].astype(float)
fdf['threads']=fdf['threads'].astype(int)

In [33]:
fdf

sec  threads      tps      read     write     other       v1      rt  \
0        1.0       64  3023.76  84691.24  38627.06  39872.91  6191.27   23.95   
1        2.0       64  3070.13  87747.71  40053.69  41543.76  6150.26   24.38   
2        3.0       64  3236.00  91827.97  42024.99  43319.99  6483.00   24.83   
3        4.0       64  3140.98  88537.38  40427.72  41828.71  6280.96   26.68   
4        5.0       64  3096.04  87770.03  40091.47  41488.49  6190.07   24.83   
...      ...      ...      ...       ...       ...       ...      ...     ...   
1795  1796.0       64  2999.99  84772.63  38729.83  40013.83  6028.97  179.94   
1796  1797.0       64  3107.95  86374.48  39354.31  40813.28  6206.89   24.83   
1797  1798.0       64  3104.05  90018.56  41106.71  42708.74  6203.11   23.10   
1798  1799.0       64  2992.93  85628.05  39033.11  40611.07  5983.86   24.38   
1799  1800.0       64  3154.62  90155.26  41107.10  42738.91  6309.25   23.95   

         v3    v4 nodes  
0      9.98  0.00     3  
1     13.00  0.00     3  
2     11.00  0.00     3  
3     11.00  0.00     3  
4     21.00  0.00     3  
...     ...   ...   ...  
1795  14.00  0.00     5  
1796  17.00  0.00     5  
1797   7.00  0.00     5  
1798   8.00  0.00     5  
1799  11.00  0.00     5  

[3600 rows x 11 columns]

In [46]:
alt.Chart(fdf,width=800,title="64 threads, 3100 tps incoming rate").mark_point(size=5).encode(
    x='sec',
    y=alt.Y('rt:Q', title="95% response time, ms"),
    color='nodes:N'
)

alt.Chart(...)

In [49]:
alt.Chart(fdf,width=800,title="64 threads, 3100 tps incoming rate").mark_point(size=5).encode(
    x='sec',
    y=alt.Y('tps:Q', title="Throughput, tps"),
    color='nodes:N'
)

alt.Chart(...)